# Dataloader for entity VGP

In [37]:
class MyConfig():
    def __init__(self):
        self.start_idx = 88888
        self.end_idx= 99999
        self.pad_idx = 80000
config = MyConfig()

In [38]:
import os
from os import listdir
from os.path import isfile, join

import numpy as np
from torch import nn

import torch.nn.functional as F
import torch.utils.data 
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence
import torchvision.models as models
from torchvision import transforms, utils

from PIL import Image
from sklearn.model_selection import train_test_split
from Flickr30kEntities.flickr30k_entities_utils import get_sentence_data, get_annotations 
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from collections import defaultdict
import time
import json



In [50]:
sentence_folder="Flickr30kEntities/Sentences/"
image_folder="Flickr30kEntities/flickr30k-images/"
annotation_folder = "Flickr30kEntities/Annotations/"
feature_folder="Entity_Resnet152/"
caption_folder="caption/"
entity_caption_path="caption/entity_dataset_train.json"

In [51]:
class EntitySupervisedDataset(Dataset):

    def __init__(self, config, feature_folder, entity_caption_path, transform=None):
        self.config = config
        self.feature_folder = feature_folder
        self.entity_caption_path = entity_caption_path
        self.transform = transform
        
        
        self.caption_names = [] # filename
        self.entity_ids = []
        self.desc_ids = []
        self.captions = []
        
        with open(entity_caption_path) as f:
            dataset = json.load(f)
        for file_item in dataset:
            filename = file_item['filename']
            for entity_item in file_item['entities']:
                entity_id = entity_item['phrase_id']
                for desc_item in entity_item['entity_descs']:
                    entity_desc_id = desc_item['entity_desc_id']
                    raw = desc_item['entity_desc'] # actually not raw, it is after processed
                    desc = desc_item['indexed']
                    # here we add START and END
                    desc = [int(self.config.start_idx)] + desc + [int(self.config.end_idx)]
                    
                    self.caption_names.append(filename)
                    self.entity_ids.append(entity_id)
                    self.desc_ids.append(entity_desc_id)
                    self.captions.append(desc)

            
    def __len__(self):
        return len(self.caption_names)

    def __getitem__(self, idx):
        filename = self.caption_names[idx]
        entity_id = self.entity_ids[idx]
        desc_id = self.desc_ids[idx]
        caption = self.captions[idx]
        image_feature = np.load(os.path.join(self.feature_folder, str(entity_id)+".npy"))
        sample = {'image': torch.tensor(image_feature), "caption": torch.tensor(caption), \
                    "caption_name": filename, "entity_id": entity_id, 'desc_id':desc_id}
        return sample
    
def entity_supervised_collate_fn(batch, config):
    """
    This is the helper function for dataloader's collate_fn
    :param batch: dict {'image': list; 'caption':list}
        image: a list contains the image tensor 
        caption: a list contains the caption tensor, padded with START and END
    :return: final_batch: dict {'image': tensor, 'caption':tensor, 'length': tensor} sorted by caption length
    """
    # sorted_batch = sorted(batch, key=lambda x: x['caption'].shape[0], reverse=True)
    image_list = [item['image'] for item in batch]
    final_images = torch.stack(image_list)
    
    caption_list = [item['caption'] for item in batch]
    caption_length = torch.tensor([len(item) for item in caption_list]).view(-1, 1)
    final_captions = pad_sequence(caption_list, batch_first=True, padding_value=config.pad_idx)

    caption_name_list = [item['caption_name'] for item in batch]
    entity_id_list = [item['entity_id'] for item in batch]
    desc_id_list = [item['desc_id'] for item in batch]
    
    final_batch = {}
    final_batch['image'] = final_images
    final_batch['caption'] = final_captions
    final_batch['length'] = caption_length
    final_batch['caption_name'] = caption_name_list
    final_batch['entity_id'] = entity_id_list
    final_batch['desc_id'] = desc_id_list
    return final_batch

In [55]:
class EntityDiscriminatorDataset(Dataset):

    def __init__(self, config, feature_folder, caption_path, transform=None):
        self.config = config
        self.feature_folder = feature_folder
        self.entity_caption_path = entity_caption_path
        self.transform = transform
        
        
        self.caption_names = [] # filename
        self.entity_ids = []
        self.desc_ids = []
        self.captions = []
    
        
        with open(entity_caption_path) as f:
            dataset = json.load(f)
        for file_item in dataset:
            filename = file_item['filename']
            for entity_item in file_item['entities']:
                entity_id = entity_item['phrase_id']
                for desc_item in entity_item['entity_descs']:
                    entity_desc_id = desc_item['entity_desc_id']
                    raw = desc_item['entity_desc'] # actually not raw, it is after processed
                    desc = desc_item['indexed']
                    # here we add START and END
                    desc = [int(self.config.start_idx)] + desc + [int(self.config.end_idx)]
                    
                    self.caption_names.append(filename)
                    self.entity_ids.append(entity_id)
                    self.desc_ids.append(entity_desc_id)
                    self.captions.append(desc)

            
    def __len__(self):
        return len(self.caption_names)

    def __getitem__(self, idx):
        filename = self.caption_names[idx]
        entity_id = self.entity_ids[idx]
        desc_id = self.desc_ids[idx]
        caption = self.captions[idx]
        image_feature = np.load(os.path.join(self.feature_folder, str(entity_id)+".npy"))
        
        
        while True:
            rand = np.random.randint(0, len(self.caption_names))
            if self.entity_ids[rand] == entity_id:
                continue
            wrong_caption = self.captions[rand]
            break
        sample = {'image': torch.tensor(image_feature), "caption": torch.tensor(caption), "wrong_caption":torch.tensor(wrong_caption), \
                    "caption_name": filename, "entity_id": entity_id, "desc_id": desc_id, \
                    "wrong_caption_name": self.caption_names[rand], "wrong_entity_id": self.entity_ids[rand], "wrong_desc_id":self.desc_ids[rand]}
        return sample
    
def entity_discriminator_collate_fn(batch, config):
    """
    This is the helper function for dataloader's collate_fn
    :param batch: dict {'image': list; 'caption':list}
        image: a list contains the image tensor 
        caption: a list contains the caption tensor, padded with START and END
    :return: final_batch: dict {'image': tensor; 
                                'caption':tensor; 
                                'length': tensor;
                                'wrong_caption': tensor; 
                                'wrong_length':tensor; } sorted by caption length (not by wrong caption length)
    """
    # sorted_batch = sorted(batch, key=lambda x: x['caption'].shape[0], reverse=True)
    image_list = [item['image'] for item in batch]
    final_images = torch.stack(image_list)
    
    caption_list = [item['caption'] for item in batch]
    caption_length = torch.tensor([len(item) for item in caption_list]).view(-1, 1)
    final_captions = pad_sequence(caption_list, batch_first=True, padding_value=config.pad_idx)
    
    wrong_caption_list = [item['wrong_caption'] for item in batch]
    wrong_caption_length = torch.tensor([len(item) for item in wrong_caption_list]).view(-1, 1)
    final_wrong_captions = pad_sequence(wrong_caption_list, batch_first=True, padding_value=config.pad_idx)

    caption_name_list = [item['caption_name'] for item in batch]
    entity_id_list = [item['entity_id'] for item in batch]
    desc_id_list = [item['desc_id'] for item in batch]
    wrong_caption_name_list = [item['wrong_caption_name'] for item in batch]
    wrong_entity_id_list = [item['wrong_entity_id'] for item in batch]
    wrong_desc_id_list = [item['wrong_desc_id'] for item in batch]
    
    final_batch = {}
    final_batch['image'] = final_images
    final_batch['caption'] = final_captions
    final_batch['length'] = caption_length
    final_batch['wrong_caption'] = final_wrong_captions
    final_batch['wrong_length'] = wrong_caption_length
    final_batch['caption_name'] = caption_name_list
    final_batch['entity_id'] = entity_id_list
    final_batch['desc_id'] = desc_id_list
    final_batch['wrong_caption_name'] = wrong_caption_name_list
    final_batch['wrong_entity_id'] = wrong_entity_id_list
    final_batch['wrong_desc_id'] = wrong_desc_id_list
    return final_batch



In [56]:
supervised_data = EntitySupervisedDataset(config, feature_folder, entity_caption_path)
supervised_loader = DataLoader(supervised_data, batch_size=256, shuffle=False, collate_fn=lambda batch: entity_supervised_collate_fn(batch, config))
discriminator_data = EntityDiscriminatorDataset(config, feature_folder, caption_path)
discriminator_loader = DataLoader(discriminator_data, batch_size=256, shuffle=False, collate_fn=lambda batch: discriminator_collate_fn(batch, config))

In [64]:
for ct, data in enumerate(discriminator_loader):
    images = data["image"]
    captions = data["caption"]
    lengths = data['length']
    wrong_captions = data["wrong_caption"]
#     print(captions, wrong_captions)
    print(captions.shape, wrong_captions.shape)
    
#     wrong_captions = data['wrong_caption']
#     wrong_lengths = data['wrong_length']
#     print(captions.shape)

torch.Size([256, 9]) torch.Size([256, 9])
torch.Size([256, 8]) torch.Size([256, 9])


AssertionError: 

# Dataloader for image captioning

In [5]:
class MyConfig():
    def __init__(self):
        self.start_index = 88888
        self.end_index= 99999
        self.pad_index = 80000
config = MyConfig()

In [1]:
import os
from os import listdir
from os.path import isfile, join

import numpy as np
from torch import nn

import torch.nn.functional as F
import torch.utils.data 
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence
import torchvision.models as models
from torchvision import transforms, utils

from PIL import Image
from sklearn.model_selection import train_test_split
from Flickr30kEntities.flickr30k_entities_utils import get_sentence_data, get_annotations 
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from collections import defaultdict
import time


In [12]:
sentence_folder="Flickr30kEntities/Sentences/"
image_folder="Flickr30kEntities/flickr30k-images/"
annotation_folder = "Flickr30kEntities/Annotations/"
feature_folder="VGG/"
caption_folder="caption/"
caption_path="caption/train_captions.txt"

In [1]:
def read_dictionary(path):
    result = {}
    with open(path, 'r') as f:
        for line in f:
            key, value = line.strip().split(' ')
            result[key] = int(value)
    return result

In [7]:
def save_dictionary(path, dictionary):
    with open(path, 'w') as f:
        for key in dictionary.keys():
            assert(" " not in key)
            f.write(key + " "+str(dictionary[key])+"\n")
def read_dictionary(path):
    result = {}
    with open(path, 'r') as f:
        for line in f:
            key, value = line.strip().split(' ')
            result[key] = int(value)
    return result

def save_captions(path, all_names, all_sentids, all_captions):
    with open(path, "w") as f:
        for i in range(len(all_captions)):
            caption = all_captions[i]
            name = all_names[i]
            sentid = str(all_sentids[i])
            to_write = name + " " + sentid + " "
            for token in caption:
                to_write += str(token) + ","
            to_write = to_write.strip(",")
            f.write(to_write + "\n")
            
def read_captions(path):
    all_names = []
    all_captions = []
    all_sentids = []
    with open(path, "r") as f:
        for line in f:
            name, sentid, raw_caption = line.strip().split(' ')
            caption = [int(item) for item in raw_caption.split(',')]
            all_names.append(name)
            all_sentids.append(int(sentid))
            all_captions.append(caption)
    return all_names, all_sentids, all_captions



In [13]:
class SupervisedDataset(Dataset):

    def __init__(self, config, feature_folder, caption_path, transform=None):
        self.config = config
        self.feature_folder = feature_folder
        self.caption_path = caption_path
        self.transform = transform
        self.caption_names, self.sentids, self.captions = read_captions(caption_path)
        
        # here we add START and END
        for i in range(len(self.captions)):
            self.captions[i] = [int(self.config.start_index)] + self.captions[i] + [int(self.config.end_index)]

            
    def __len__(self):
        return len(self.caption_names)

    def __getitem__(self, idx):
        filename = self.caption_names[idx]
        caption = self.captions[idx]
        image_feature = np.load(os.path.join(feature_folder, filename)+".npy")
        sample = {'image': torch.tensor(image_feature), "caption": torch.tensor(caption)}
        return sample
    
def supervised_collate_fn(batch, config):
    """
    This is the helper function for dataloader's collate_fn
    :param batch: dict {'image': list; 'caption':list}
        image: a list contains the image tensor 
        caption: a list contains the caption tensor, padded with START and END
    :return: final_batch: dict {'image': tensor, 'caption':tensor, 'length': tensor} sorted by caption length
    """
    sorted_batch = sorted(batch, key=lambda x: x['caption'].shape[0], reverse=True)
    image_list = [item['image'] for item in sorted_batch]
    final_images = torch.stack(image_list)
    
    caption_list = [item['caption'] for item in sorted_batch]
    caption_length = torch.tensor([len(item) for item in caption_list]).view(-1, 1)
    max_length = len(caption_list[0])
    final_captions = pad_sequence(caption_list, batch_first=True, padding_value=config.pad_index)
    
    final_batch = {}
    final_batch['image'] = final_images
    final_batch['caption'] = final_captions
    final_batch['length'] = caption_length
    return final_batch

In [24]:
class DiscriminatorDataset(Dataset):

    def __init__(self, config, feature_folder, caption_path, transform=None):
        self.config = config
        self.feature_folder = feature_folder
        self.caption_path = caption_path
        self.transform = transform  
        self.caption_names, self.sentids, self.captions = read_captions(caption_path)
        
        # here we add START and END
        for i in range(len(self.captions)):
            self.captions[i] = [int(self.config.start_index)] + self.captions[i] + [int(self.config.end_index)]

            
    def __len__(self):
        return len(self.caption_names)

    def __getitem__(self, idx):
        filename = self.caption_names[idx]
        caption = self.captions[idx]
        image_feature = np.load(os.path.join(feature_folder, filename)+".npy")
        
        
        while True:
            rand = np.random.randint(0, len(self.caption_names))
            if self.caption_names[rand] == filename:
                continue
            wrong_caption = self.captions[rand]
            break
        sample = {'image': torch.tensor(image_feature), "caption": torch.tensor(caption), "wrong_caption":torch.tensor(wrong_caption)}
        return sample
    
def discriminator_collate_fn(batch, config):
    """
    This is the helper function for dataloader's collate_fn
    :param batch: dict {'image': list; 'caption':list}
        image: a list contains the image tensor 
        caption: a list contains the caption tensor, padded with START and END
    :return: final_batch: dict {'image': tensor; 
                                'caption':tensor; 
                                'length': tensor;
                                'wrong_caption': tensor; 
                                'wrong_length':tensor; } sorted by caption length (not by wrong caption length)
    """
    sorted_batch = sorted(batch, key=lambda x: x['caption'].shape[0], reverse=True)
    image_list = [item['image'] for item in sorted_batch]
    final_images = torch.stack(image_list)
    
    caption_list = [item['caption'] for item in sorted_batch]
    caption_length = torch.tensor([len(item) for item in caption_list]).view(-1, 1)
    max_length = len(caption_list[0])
    final_captions = pad_sequence(caption_list, batch_first=True, padding_value=config.pad_index)
    
    wrong_caption_list = [item['wrong_caption'] for item in sorted_batch]
    wrong_caption_length = torch.tensor([len(item) for item in wrong_caption_list]).view(-1, 1)
    wrong_max_length = wrong_caption_length.max().item()
    final_wrong_captions = pad_sequence(wrong_caption_list, batch_first=True, padding_value=config.pad_index)
    
    final_batch = {}
    final_batch['image'] = final_images
    final_batch['caption'] = final_captions
    final_batch['length'] = caption_length
    final_batch['wrong_caption'] = final_wrong_captions
    final_batch['wrong_length'] = wrong_caption_length
    return final_batch


In [25]:
test_data = SupervisedDataset(config, feature_folder, caption_path)
test_loader = DataLoader(test_data, batch_size=256, shuffle=False, collate_fn=lambda batch: supervised_collate_fn(batch, config))
discriminator_data = DiscriminatorDataset(config, feature_folder, caption_path)
discriminator_loader = DataLoader(discriminator_data, batch_size=256, shuffle=False, collate_fn=lambda batch: discriminator_collate_fn(batch, config))

In [26]:
for ct, data in enumerate(discriminator_loader):
    images = data["image"]
    captions = data["caption"]
    lengths = data['length']
    wrong_captions = data['wrong_caption']
    wrong_lengths = data['wrong_length']
    print(images.shape)

aaaaa
2457052334 1000092795
aaaaa
4926690990 1000092795
aaaaa
294353408 1000092795
aaaaa
4784479869 1000092795
aaaaa
49553964 1000092795
aaaaa
4748798432 10002456
aaaaa
3337113147 10002456
aaaaa
3060537675 10002456
aaaaa
3666796674 10002456
aaaaa
3534172926 10002456
aaaaa
3504222146 1000268201
aaaaa
425088533 1000268201
aaaaa
3687996569 1000268201
aaaaa
2172574039 1000268201
aaaaa
3170074597 1000268201
aaaaa
570990225 1000344755
aaaaa
816084977 1000344755
aaaaa
4714815517 1000344755
aaaaa
390902331 1000344755
aaaaa
101001624 1000344755
aaaaa
4546664216 1000366164
aaaaa
50835360 1000366164
aaaaa
3627290893 1000366164
aaaaa
201995559 1000366164
aaaaa
4781925272 1000366164
aaaaa
3550276904 1000523639
aaaaa
150710406 1000523639
aaaaa
3197194113 1000523639
aaaaa
3320411267 1000523639
aaaaa
2913965136 1000523639
aaaaa
947969010 1000919630
aaaaa
3425917247 1000919630
aaaaa
161661145 1000919630
aaaaa
4824738139 1000919630
aaaaa
123728333 1000919630
aaaaa
1237177353 10010052
aaaaa
3299418821 10

aaaaa
2385744837 103631543
aaaaa
2934325103 103631543
aaaaa
38110161 103631543
aaaaa
391020801 103631543
aaaaa
40199801 1039360778
aaaaa
6848902929 1039360778
aaaaa
2502248149 1039360778
aaaaa
2474918824 1039360778
aaaaa
7832183018 1039360778
aaaaa
846516819 103953336
aaaaa
4574105974 103953336
aaaaa
4225248313 103953336
aaaaa
4022170842 103953336
aaaaa
2288315705 103953336
aaaaa
514990193 10404007
aaaaa
4342753575 10404007
aaaaa
2324842927 10404007
aaaaa
4675748463 10404007
aaaaa
101669240 10404007
aaaaa
3456579559 1040426962
aaaaa
3636247381 1040426962
aaaaa
3715635007 1040426962
aaaaa
6029710737 1040426962
aaaaa
3530087422 1040426962
aaaaa
2983555530 104136873
aaaaa
3888575744 104136873
aaaaa
6556869275 104136873
aaaaa
4857778452 104136873
aaaaa
2861413434 104136873
aaaaa
3561498139 104180524
aaaaa
301746481 104180524
aaaaa
3327487011 104180524
aaaaa
194464865 104180524
aaaaa
40738998 104180524
aaaaa
2882483779 1042020065
aaaaa
4784874051 1042020065
aaaaa
4789705901 1042020065
aaaaa

aaaaa
1096800382 1088767354
aaaaa
4695704555 1088767354
aaaaa
4803245860 1088767354
aaaaa
3250589803 1088767354
aaaaa
3087243192 1088767354
aaaaa
3439087390 108898978
aaaaa
7425128736 108898978
aaaaa
19719902 108898978
aaaaa
4762718110 108898978
aaaaa
5381102989 108898978
aaaaa
4830215458 108899015
aaaaa
4831642430 108899015
aaaaa
141736784 108899015
aaaaa
7785430960 108899015
aaaaa
363056425 108899015
aaaaa
3427540832 1089181217
aaaaa
2172570753 1089181217
aaaaa
5904834587 1089181217
aaaaa
3173928684 1089181217
aaaaa
4942571466 1089181217
aaaaa
4439099586 1089354362
aaaaa
6678735 1089354362
aaaaa
2311401527 1089354362
aaaaa
3621095412 1089354362
aaaaa
2600065074 1089354362
aaaaa
4622379849 108957912
aaaaa
3698350607 108957912
aaaaa
879043160 108957912
aaaaa
3526461098 108957912
aaaaa
2272750492 108957912
aaaaa
3533928622 108970557
aaaaa
2525455265 108970557
aaaaa
1228304869 108970557
aaaaa
4119940755 108970557
aaaaa
2888499869 108970557
aaaaa
3576536763 1089755335
aaaaa
4634174359 108

aaaaa
2332186035 112178718
aaaaa
29813421 112178718
aaaaa
3482473245 11220707
aaaaa
4592144166 11220707
aaaaa
4888936808 11220707
aaaaa
154873964 11220707
aaaaa
4717494930 11220707
aaaaa
3361279771 1122177096
aaaaa
2088460083 1122177096
aaaaa
110615445 1122177096
aaaaa
2626553824 1122177096
aaaaa
5989324335 1122177096
aaaaa
2957681960 112220869
aaaaa
5076224694 112220869
aaaaa
7523563426 112220869
aaaaa
3215896272 112220869
aaaaa
2194797921 112220869
aaaaa
2608623292 1122357785
aaaaa
2575887239 1122357785
aaaaa
4503962385 1122357785
aaaaa
4465873363 1122357785
aaaaa
4441947902 1122357785
aaaaa
3202592293 112245524
aaaaa
24186977 112245524
aaaaa
1435194718 112245524
aaaaa
2215767852 112245524
aaaaa
177522874 112245524
aaaaa
4622340284 1122579380
aaaaa
5823148675 1122579380
aaaaa
416272701 1122579380
aaaaa
5187127204 1122579380
aaaaa
52581560 1122579380
aaaaa
4912991926 112264837
aaaaa
3702436188 112264837
aaaaa
3166578139 112264837
aaaaa
1191939974 112264837
aaaaa
4685167138 112264837
a

aaaaa
191652362 1145145003
aaaaa
106027978 1145718750
aaaaa
2971431335 1145718750
aaaaa
136644885 1145718750
aaaaa
2452686995 1145718750
aaaaa
4977898090 1145718750
aaaaa
209604956 1145722716
aaaaa
24188477 1145722716
aaaaa
4568594263 1145722716
aaaaa
6980999098 1145722716
aaaaa
462725077 1145722716
aaaaa
1994416869 1145730606
aaaaa
7847188568 1145730606
aaaaa
7602898434 1145730606
aaaaa
31764678 1145730606
aaaaa
4533155215 1145730606
aaaaa
4788709442 1145755142
aaaaa
4480006240 1145755142
aaaaa
160805827 1145755142
aaaaa
5880786104 1145755142
aaaaa
3072172967 1145755142
aaaaa
2863027424 1145770960
aaaaa
4818829454 1145770960
aaaaa
4304306426 1145770960
aaaaa
2911552402 1145770960
aaaaa
4018317730 1145770960
aaaaa
4691807711 1145781754
aaaaa
85306247 1145781754
aaaaa
2345980168 1145781754
aaaaa
161240978 1145781754
aaaaa
4824240641 1145781754
aaaaa
70645290 1145810912
aaaaa
6960188329 1145810912
aaaaa
3708441539 1145810912
aaaaa
3405336889 1145810912
aaaaa
508537723 1145810912
aaaaa
47

...

aaaaa
2638512789 837893113
aaaaa
7248245932 837893113
aaaaa
31648340 837893113
aaaaa
6287749306 837919879
aaaaa
2889358507 837919879
aaaaa
3097037008 837919879
aaaaa
3368569524 837919879
aaaaa
4585566336 837919879
aaaaa
3560977956 838074897
aaaaa
4633043171 838074897
aaaaa
5730792187 838074897
aaaaa
4725723908 838074897
aaaaa
2402793046 838074897
aaaaa
3313620862 839295615
aaaaa
2564888404 839295615
aaaaa
2868798 839295615
aaaaa
4718134968 839295615
aaaaa
4828143860 839295615
aaaaa
3030953639 840202638
aaaaa
314940358 840202638
aaaaa
6696219 840202638
aaaaa
3203593191 840202638
aaaaa
7165826558 840202638
aaaaa
2645745905 8404753
aaaaa
5922967014 8404753
aaaaa
1423449879 8404753
aaaaa
3563668905 8404753
aaaaa
4978374359 8404753
aaaaa
6414597073 842263436
aaaaa
3203742047 842263436
aaaaa
4656684238 842263436
aaaaa
2876994989 842263436
aaaaa
2317271 842263436
aaaaa
4152834507 84291062
aaaaa
2768292531 84291062
aaaaa
1301978702 84291062
aaaaa
4762784528 84291062
aaaaa
842960985 84291062
aa

aaaaa
4475333077 862683343
aaaaa
2568347901 862683343
aaaaa
3928848343 86288449
aaaaa
2873065944 86288449
aaaaa
2659606300 86288449
aaaaa
444845904 86288449
aaaaa
4881309019 86288449
aaaaa
2748403765 86289690
aaaaa
2127166904 86289690
aaaaa
4860102706 86289690
aaaaa
4447502217 86289690
aaaaa
2745588751 86289690
aaaaa
184037893 86289696
aaaaa
111390902 86289696
aaaaa
141139674 86289696
aaaaa
4936286470 86289696
aaaaa
4629445758 86289696
aaaaa
4044612196 86289724
aaaaa
2858843359 86289724
aaaaa
3631810528 86289724
aaaaa
1463732130 86289724
aaaaa
1130295306 86289724
aaaaa
7831143656 863036078
aaaaa
32473949 863036078
aaaaa
2470486377 863036078
aaaaa
2298946012 863036078
aaaaa
313542438 863036078
aaaaa
2954929479 86341446
aaaaa
99171998 86341446
aaaaa
209274114 86341446
aaaaa
94987177 86341446
aaaaa
2241665783 86341446
aaaaa
6947639624 86343902
aaaaa
249394748 86343902
aaaaa
160128865 86343902
aaaaa
4941244018 86343902
aaaaa
4726111025 86343902
aaaaa
2230813326 863901193
aaaaa
4801216793 8

aaaaa
6066197286 89332423
aaaaa
3846674484 89332423
aaaaa
2426958307 89332423
aaaaa
5476674072 89332423
aaaaa
4875329519 89353191
aaaaa
3054200086 89353191
aaaaa
3229898555 89353191
aaaaa
6785193001 89353191
aaaaa
2052953131 89353191
aaaaa
4944653840 893808757
aaaaa
2230693384 893808757
aaaaa
3327761688 893808757
aaaaa
2072907691 893808757
aaaaa
1300075854 893808757
aaaaa
1629314152 89404014
aaaaa
5501226985 89404014
aaaaa
460195312 89404014
aaaaa
4461720604 89404014
aaaaa
2555545571 89404014
aaaaa
3609377404 89407459
aaaaa
2605373150 89407459
aaaaa
3798592106 89407459
aaaaa
4922687043 89407459
aaaaa
170737141 89407459
aaaaa
2253938667 894928353
aaaaa
2446839286 894928353
aaaaa
3698928767 894928353
aaaaa
3687736666 894928353
aaaaa
230339366 894928353
aaaaa
2446928775 894964960
aaaaa
360132352 894964960
aaaaa
2683823978 894964960
aaaaa
4009638392 894964960
aaaaa
4821989284 894964960
aaaaa
1231229740 89505897
aaaaa
255863389 89505897
aaaaa
606691813 89505897
aaaaa
4857709036 89505897
aaa

aaaaa
3304556387 938661426
aaaaa
4109577038 938661426
aaaaa
4364402091 93922153
aaaaa
3890244554 93922153
aaaaa
4886651712 93922153
aaaaa
2396691909 93922153
aaaaa
475317104 93922153
aaaaa
6993511259 94062798
aaaaa
153299765 94062798
aaaaa
3028095878 94062798
aaaaa
2602679255 94062798
aaaaa
254901702 94062798
aaaaa
3928046645 940973925
aaaaa
6473658663 940973925
aaaaa
402229993 940973925
aaaaa
4668948309 940973925
aaaaa
298122528 940973925
aaaaa
110964272 941641803
aaaaa
540943543 941641803
aaaaa
4464415997 941641803
aaaaa
4821884870 941641803
aaaaa
4482794481 941641803
aaaaa
2437917174 94183012
aaaaa
4745224936 94183012
aaaaa
3757332635 94183012
aaaaa
2971431335 94183012
aaaaa
848007330 94183012
aaaaa
661749711 94232465
aaaaa
535179217 94232465
aaaaa
3980921026 94232465
aaaaa
2815755985 94232465
aaaaa
2495204443 94232465
aaaaa
4742814797 942399470
aaaaa
5676123833 942399470
aaaaa
3026102616 942399470
aaaaa
3665421893 942399470
aaaaa
2170222061 942399470
aaaaa
4803984649 9426826
aaaaa


aaaaa
3472364264 969779007
aaaaa
3189941492 969779007
aaaaa
4637466845 96978713
aaaaa
3364247489 96978713
aaaaa
3970504937 96978713
aaaaa
2189995738 96978713
aaaaa
4954782761 96978713
aaaaa
3837069734 96985174
aaaaa
433810429 96985174
aaaaa
3321832766 96985174
aaaaa
3217910740 96985174
aaaaa
136358691 96985174
aaaaa
4504478051 970641406
aaaaa
4392524083 970641406
aaaaa
5253872191 970641406
aaaaa
5039758111 970641406
aaaaa
3016200560 970641406
aaaaa
7773468788 970958470
aaaaa
4912471031 970958470
aaaaa
2187356302 970958470
aaaaa
4926983629 970958470
aaaaa
4533655072 970958470
aaaaa
4304306426 97105139
aaaaa
2705099783 97105139
aaaaa
6242324579 97105139
aaaaa
4796004241 97105139
aaaaa
213980367 97105139
torch.Size([256, 4096])
aaaaa
54260190 97131520
aaaaa
6445655263 97131520
aaaaa
6154676236 97131520
aaaaa
2412716991 97131520
aaaaa
261436644 97131520
aaaaa
384594338 97138308
aaaaa
492493570 97138308
aaaaa
480653124 97138308
aaaaa
236223192 97138308
aaaaa
4789755167 97138308
aaaaa
170717

In [22]:
a = torch.ones((3))
b = torch.zeros((3))


In [23]:
torch.stack([a,b])

tensor([[1., 1., 1.],
        [0., 0., 0.]])

In [7]:
from torch.nn.utils.rnn import pad_sequence
a = torch.zeros(10, 300)
b = torch.ones(22, 300)
c = torch.ones(15, 300)*2
pad_sequence([a, b, c])

tensor([[[0., 0., 0.,  ..., 0., 0., 0.],
         [1., 1., 1.,  ..., 1., 1., 1.],
         [2., 2., 2.,  ..., 2., 2., 2.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [1., 1., 1.,  ..., 1., 1., 1.],
         [2., 2., 2.,  ..., 2., 2., 2.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [1., 1., 1.,  ..., 1., 1., 1.],
         [2., 2., 2.,  ..., 2., 2., 2.]],

        ...,

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [1., 1., 1.,  ..., 1., 1., 1.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [1., 1., 1.,  ..., 1., 1., 1.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [1., 1., 1.,  ..., 1., 1., 1.],
         [0., 0., 0.,  ..., 0., 0., 0.]]])

In [5]:
a = torch.tensor([1,2,3])

In [4]:
b = torch.tensor([2,2,2], dtype=torch.float)

In [6]:
a[b]

IndexError: tensors used as indices must be long, byte or bool tensors

In [3]:
device = torch.device('cuda:3' if torch.cuda.is_available() else 'cpu')
print(device)

cuda:3


In [38]:
aa = a.to(device)

In [39]:
mask = np.array([0,2,1])

In [42]:
aa[[True,False,True]]

tensor([1, 3], device='cuda:4')